# Momentum Score Card
<img src=https://kennysantos.com/wp-content/uploads/2015/07/Final-Momentum-Logo-1024x689.jpg width="500">

**Reminder**: _refresh Bloomberg data_ **<!>**

In [1]:
import pandas as pd
from datetime import timedelta, date, datetime
import calendar
import datetime

## read the date from Bloomberg about Total Return Index Gross Dividend
df=pd.read_excel('Russell 2000 Index.xlsx', 'totret') 

In [2]:
## DATA CURATION
#backfill NA
df=df.fillna(method="bfill")
#drop NA columns
pd.DataFrame.dropna(df,axis=1, inplace=True) #<---- this is the problem
df.drop(df.index[0], inplace=True)

#lag the column names
l=list(df.columns)
new_l=["Date",]
for i in range(-1,len(l)-2):
    new_l.append(l[i+1])
    
df.columns=new_l
#take only the meaningful columns 
df_ticker=df[df.columns[1::2]]
df_ticker.index=df[df.columns[0]]

In [3]:
## Create a index of day which contains only the business days from Monday to Friday
def daterange(date1, date2):
    for n in range(int ((date2 - date1).days)+1):
        yield date1 + timedelta(n)

start_dt = date(2017, 12, 31)
end_dt = date(2022, 1, 1)
date=[]
for dt in daterange(start_dt, end_dt):
    date.append(dt.strftime("%Y-%m-%d"))

number_weeklyday=[]
for i in date:
    strip_date=datetime.datetime.strptime(i, "%Y-%m-%d" )
    weeklyday=calendar.weekday(strip_date.year,strip_date.month,strip_date.day)+1
    if (weeklyday<6) & (weeklyday>=1):
        number_weeklyday.append(i)

In [4]:
b_day=pd.Series(number_weeklyday, name="Business Day") ## generate a final pandas.Series
today_date_10lag=[datetime.datetime.today().strftime("%Y-%m-%d")]
start_index=b_day[b_day.isin(today_date_10lag)==True].index[0]

## generate the next 10 days index
Lag_10days=[]
for i in range(0,10):
    Lag_10days.append(list(b_day[b_day.index==start_index+i]))
Lag_10days=[item for sublist in Lag_10days for item in sublist]


In [5]:
## generate a list of date which contains the future 10 days index back lag to 79 days ago 
n_79d=list(b_day[b_day.isin(Lag_10days)==True].index-79)
Lag_79d=list(b_day[b_day.index.isin(n_79d)==True].values) 
## generate a list of date which contains the future 10 days index back lag to 9 days ago 
n_9d=list(b_day[b_day.isin(Lag_10days)==True].index-9)
Lag_9d=list(b_day[b_day.index.isin(n_9d)==True].values)

In [6]:
ticker=list(df_ticker.columns) ## ticker list included in Dow Jones Industrial Average Index

In [7]:
## Calculate the past 70 days tota return %
df_totret=pd.DataFrame(columns=ticker, index=Lag_10days)
ress=[]
for i in range(0,len(Lag_9d)):
    
    res=((pd.DataFrame(df_ticker[(df_ticker.index==Lag_9d[i])==True].T).values/pd.DataFrame(df_ticker[(df_ticker.index==Lag_79d[i])==True].T).values)-1)*100
    ress.append(res)
    ## attach the result into the DataFrame
    for j in range(0, len(ticker)):
        df_totret.iloc[i,j]=float(ress[i][j])

In [8]:
final_totret=df_totret.T
final_totret ## Final table with the 70 days tota return % for each costituents of the Index

2020-02-24 2020-02-25 2020-02-26 2020-02-27 2020-02-28  \
AAN UN Equity    -10.4958   -7.07807   -2.73451  0.0328284    1.51496   
AAOI UQ Equity     1.5887    6.40478    19.2703      9.375   -2.05761   
AAON UW Equity       11.2    12.6472    14.1586    14.2332     13.915   
AAT UN Equity    -3.03666   -2.10842   -1.41014   0.453632   0.132361   
AAWW UW Equity     3.1619    5.61323  -0.113379    2.32297     3.8403   
AAXN UW Equity    64.1518     68.415    67.4108    33.4303     35.159   
ABCB UW Equity   -5.49354   -5.78413   -6.33835   -7.34854    -7.0557   
ABEO UR Equity    17.9104    21.4559    13.6029    20.5323    27.3092   
ABG UN Equity    -8.33257   -9.98423   -10.3949   -12.2501   -12.8812   
ABM UN Equity     4.93211    6.00877    5.05586     3.3079    3.66428   
ABTX UQ Equity    9.19475    9.12981    8.97508    9.20455    8.83352   
AC UN Equity      6.83858    8.98714    9.99493    11.8148    11.2438   
ACA UN Equity     15.6383      19.69    23.3759    21.0215    21.8047   
ACAD UW Equity    5.43008    10.3196    13.7621     8.1671    1.87887   
ACBI UW Equity    1.89274    3.21222    5.37408    5.78249    5.22427   
ACCO UN Equity   -2.48794    11.0449     9.3324    5.46001    5.00958   
ACER UR Equity    43.9024      46.13    45.0311    44.1718    39.0533   
ACIA UW Equity    4.46855    4.05446    3.99516    3.59777    3.02395   
ACIW UW Equity     10.796    12.3972    4.91176    4.50581    6.72406   
ACLS UW Equity    31.3242    31.1661    31.5523    29.4333    26.6547   
ACNB UR Equity     1.3551    1.75727   0.534215   -1.03954   -1.15173   
ACOR UW Equity   -16.8067   -19.2771    -20.332   -23.5043   -18.2648   
ACRE UN Equity    10.8695    10.9385    11.7276     12.457    11.6554   
ACRS UW Equity   -19.4118   -14.8148   -18.3432   -30.7692   -28.5714   
ACRX UQ Equity   -15.7635   -11.5183      -16.5   -17.5258   -10.1124   
ACTG UW Equity         -2   0.406504   -4.70588   -5.03876   -6.13027   
ADC UN Equity     1.87986   0.666452    2.55829    4.88665    5.12654   
ADES UQ Equity   -9.21034   -8.24332   -6.22513   -3.59953   -2.99434   
ADMA UQ Equity   -30.2529   -28.1124   -22.3451   -18.5615   -20.0456   
ADMS UQ Equity    29.8611    33.5202    22.3404   -0.35524    4.08163   
...                   ...        ...        ...        ...        ...   
XAN UN Equity     6.46784    7.68285    7.95456    7.94931    7.39766   
XBIT UW Equity    107.832    110.425    57.1293     35.798      35.31   
XELA UR Equity   -50.2187   -44.4831   -49.4951   -46.1607   -49.6609   
XENT UQ Equity    24.8269    24.9423    33.4571    35.7377    38.5277   
XERS UW Equity   -50.6271   -54.8206   -49.8177   -50.1247   -52.7187   
XFOR UR Equity   -21.1585   -29.4892   -33.4079   -31.5476   -35.2113   
XGN UQ Equity    -4.07407   -11.4818   -2.73055    9.06266    6.57895   
XHR UN Equity    -10.7305   -8.41918   -6.59945    -6.8458   -6.53731   
XLRN UQ Equity    96.7241    136.677    131.741    116.405    110.141   
XNCR UQ Equity    11.8644    8.87485    11.8473    9.71137    7.64012   
XOG UW Equity    -50.4425   -45.1456   -54.2601   -55.5888   -49.1765   
XPER UW Equity    -25.904   -23.6395   -26.7658   -28.3052   -27.1168   
XXII UA Equity   -42.9379   -34.3373   -29.1139        -30   -28.6624   
YCBD UA Equity   -70.9763   -69.8701   -71.3217   -70.1754   -68.5185   
YELP UN Equity    4.82509     8.1015    21.1819    1.32298   -2.30172   
YETI UN Equity    7.40508    12.9841    17.2497    7.88436    7.99079   
YEXT UN Equity  -0.552147   0.505689    1.50849   0.124224  -0.616523   
YGYI UR Equity   -67.8005   -66.7458   -66.3551    -64.878        -64   
YMAB UW Equity    10.8297         14    13.4237    14.9582    13.6505   
YORW UW Equity    13.2666    14.3968    17.6627    16.5632    17.0397   
YRCW UW Equity   -43.1981   -39.4799        -45   -45.5399   -43.8257   
ZAGG UW Equity  -0.719424    16.9399   -1.42857   -1.18064  -0.357143   
ZEUS UW Equity   -6.80528    -7.0047   -10.1785    1.24112     -2.448   


In [9]:
## Rank the total return 70 days from 1-30 (1: as largest 70d tot ret)
s=pd.DataFrame()
for i in final_totret.columns:
    res=final_totret[i].rank(ascending=0).sort_values().index
    s[i]=res

In [10]:
s.index=list(range(1,1976)) 

### How you read the table below?

**The main goal here is to invest in the stocks that appear at the first 10 positions in last column (the date at the end of the next 10 days) of the DataSet in order to build a Momentum Portfolio based on the past 70days total return - MOM Line.**

_Momentum=V−Vx_

where:
V=Latest price
Vx=Closing price
x=Number of days ago



For Example: On 2020-March-05 The Portolio should contain the following 10 stocks:
- BIOXCEL THERAPEUTICS INC	
- CHEMOCENTRYX INC	
- FORTY SEVEN INC		
- ADURO BIOTECH INC	
- AXSOME THERAPEUTICS INC
- TOCAGEN INC
- MERSANA THERAPEUTICS INC	
- AKEBIA THERAPEUTICS INC
- ENPHASE ENERGY INC
- SAVARA INC


In [11]:
s 

2020-02-24      2020-02-25      2020-02-26      2020-02-27  \
1     FTSV UW Equity  KRTX UQ Equity  BTAI UR Equity  BTAI UR Equity   
2     KRTX UQ Equity  FTSV UW Equity  KRTX UQ Equity  KRTX UQ Equity   
3     BTAI UR Equity  CCXI UW Equity  FTSV UW Equity  FTSV UW Equity   
4     CCXI UW Equity  BTAI UR Equity  CCXI UW Equity  CCXI UW Equity   
5     MRSN UW Equity  MRSN UW Equity  MRSN UW Equity  MRSN UW Equity   
6     AXSM UQ Equity  AXSM UQ Equity  AXSM UQ Equity  AXSM UQ Equity   
7     APLT UQ Equity  APLT UQ Equity  ADRO UW Equity  APLT UQ Equity   
8      KOD UQ Equity   KOD UQ Equity  APLT UQ Equity  CRTX UW Equity   
9     CLVS UW Equity  VBIV UR Equity  VBIV UR Equity  SVRA UW Equity   
10      BE UN Equity  CRTX UW Equity   KOD UQ Equity  ADRO UW Equity   
11    VBIV UR Equity    BE UN Equity  SVRA UW Equity  VBIV UR Equity   
12    CRTX UW Equity  CLVS UW Equity  CRTX UW Equity   KOD UQ Equity   
13    FULC UQ Equity  SVRA UW Equity  KNSA UW Equity  CDLX UQ Equity   
14    ADRO UW Equity  ADRO UW Equity  MIRM UQ Equity  MIRM UQ Equity   
15     CBB UN Equity  KNSA UW Equity  AKBA UQ Equity  ITCI UW Equity   
16    MIRM UQ Equity   CBB UN Equity  ITCI UW Equity   CBB UN Equity   
17    SVRA UW Equity  FULC UQ Equity   CBB UN Equity  KNSA UW Equity   
18    KNSA UW Equity  RTIX UW Equity  CDLX UQ Equity  ENPH UQ Equity   
19    CNST UW Equity  XLRN UQ Equity  XLRN UQ Equity  RTIX UW Equity   
20    AKBA UQ Equity  ARVN UW Equity  RTIX UW Equity  BREW UW Equity   
21    CDLX UQ Equity  AKBA UQ Equity  ENPH UQ Equity  FULC UQ Equity   
22     CUE UR Equity  MIRM UQ Equity  FULC UQ Equity  XLRN UQ Equity   
23    ARVN UW Equity  ENPH UQ Equity  CLVS UW Equity  AKBA UQ Equity   
24    RTIX UW Equity  CDLX UQ Equity    BE UN Equity  OYST UW Equity   
25    ITCI UW Equity   CUE UR Equity   CUE UR Equity  CYCN UW Equity   
26    MNTA UW Equity  ITCI UW Equity  BREW UW Equity    BE UN Equity   
27    BREW UW Equity  OYST UW Equity   CVM UA Equity  PRNB UW Equity   
28    RAPT UQ Equity  PRNB UW Equity  PRNB UW Equity   CVM UA Equity   
29    TEUM UR Equity  WRTC UR Equity  OYST UW Equity  IMGN UW Equity   
30    ENPH UQ Equity  BREW UW Equity  ARVN UW Equity  AVXL UR Equity   
...              ...             ...             ...             ...   
1946  HNRG UR Equity   PHX UN Equity  CFMS UW Equity  XERS UW Equity   
1947  ROSE UR Equity  IDEX UR Equity    SD UN Equity  CFMS UW Equity   
1948  PTLA UW Equity  XERS UW Equity  PTLA UW Equity  PACD UN Equity   
1949   CBL UN Equity  HNRG UR Equity   PHX UN Equity  PTLA UW Equity   
1950   BXC UN Equity   CBL UN Equity   PYX UN Equity    SD UN Equity   
1951   RLH UN Equity   BGG UN Equity   BGG UN Equity   PHX UN Equity   
1952  PRTY UN Equity  ANAB UW Equity   XOG UW Equity   XOG UW Equity   
1953  ANAB UW Equity   PYX UN Equity  HNRG UR Equity   CBL UN Equity   
1954   BGG UN Equity  PRTY UN Equity   CBL UN Equity   BGG UN Equity   
1955  SBOW UN Equity   RLH UN Equity  ANAB UW Equity   PYX UN Equity   
1956  CONN UW Equity  CONN UW Equity   RLH UN Equity  HNRG UR Equity   
1957  GLOG UN Equity   WLL UN Equity  IDEX UR Equity  IDEX UR Equity   
1958   PLT UN Equity  SBOW UN Equity  TRXC UA Equity  TRXC UA Equity   
1959  EXTN UN Equity  EXTN UN Equity  CONN UW Equity  CONN UW Equity   
1960  FTSI UN Equity  KLXE UW Equity   WLL UN Equity   WLL UN Equity   
1961  KLXE UW Equity  TRXC UA Equity  SPPI UW Equity  YGYI UR Equity   
1962  SPPI UW Equity  SPPI UW Equity  KLXE UW Equity  GPOR UW Equity   
1963  TRXC UA Equity  FTSI UN Equity  GPOR UW Equity  KLXE UW Equity   
1964  YGYI UR Equity  GPOR UW Equity  YGYI UR Equity  SPPI UW Equity   
1965  GPOR UW Equity  YGYI UR Equity  SBOW UN Equity   UNT UN Equity   
1966  CBAY UW Equity  AKRX UW Equity   WVE UQ Equity  CTRA UN Equity   
1967  AKRX UW Equity  SLDB UW Equity  SLDB UW Equity  AKRX UW Equity   
1968  YCBD UA Equity  YCBD UA Equity  CTRA UN Equity  YCBD UA Equity   
1969   WVE UQ Equity   WVE UQ Equity  YCBD UA Equi

### News Qualitative Analysis Top 10


By looking from the prospective of a LONG investors, Bloomberg use Supervised Machine Learning algorithm in order to classify between -1 (bad news) and 1(good news) - with 0 being neutral - the text information collected from the market/social media in the past 8h. 

In [12]:
top_10=s.iloc[0:10,9:10]
top_10.columns=["Ticker"]

In [13]:
## read the date from Bloomberg about NEWS sentiment analysis 8h 
news=pd.read_excel('Russell 2000 Index.xlsx', 'ML_SENTIMENT_NEWS') 

In [14]:
news.columns=["Ticker", "Name","NEWS_SENTIMENT", "Industry" ]
news = news.iloc[1:]
news=news.iloc[:,0:4]

As we can observe from below AARON's Inc has got a negative sentiment score, thus this type of stocks are excluded from the Investment Portofolio considered in the last of the 10 days ranking. 

In [15]:
def highlight(s):
    if s.NEWS_SENTIMENT > 0:
        return ['background-color: springgreen']*4
    elif s.NEWS_SENTIMENT < 0:
        return ['background-color: tomato']*4
    else:
        return ['background-color: white']*4
 
 
news.style.apply(highlight, axis=1)

In [16]:
top_10_news=pd.merge(top_10,news)
def highlight_neg(s):
    if s.NEWS_SENTIMENT < 0:
        return ['background-color: tomato']*4
    else:
        return ['background-color: white']*4
top_10_news.style.apply(highlight_neg, axis=1)

In [17]:
P_N_news= news[ news['NEWS_SENTIMENT'] >=0 ] ## sort by positive and neutral news 
last_col=s.iloc[:,9:10]
last_col.columns=["Ticker"]
## pick the top 10 companies that do not have the negative sentiment indicator 
Final_TOP10=pd.merge(last_col,P_N_news).iloc[0:10,] 

#### _Final Portofolio with Momentum strategy 70 days tot return gross DVDs sort by positive/neutral sentiment news_ :

In [18]:
Final_TOP10

Ticker                      Name NEWS_SENTIMENT  \
0  BTAI UR Equity  BIOXCEL THERAPEUTICS INC       0.159411   
1  CCXI UW Equity          CHEMOCENTRYX INC              0   
2  FTSV UW Equity           FORTY SEVEN INC              0   
3  ADRO UW Equity         ADURO BIOTECH INC              0   
4  AXSM UQ Equity   AXSOME THERAPEUTICS INC              0   
5  TOCA UW Equity               TOCAGEN INC              0   
6  MRSN UW Equity  MERSANA THERAPEUTICS INC              0   
7  AKBA UQ Equity   AKEBIA THERAPEUTICS INC       0.106781   
8  ENPH UQ Equity        ENPHASE ENERGY INC              0   
9  SVRA UW Equity                SAVARA INC              0   

                 Industry  
0  Consumer, Non-cyclical  
1  Consumer, Non-cyclical  
2  Consumer, Non-cyclical  
3  Consumer, Non-cyclical  
4  Consumer, Non-cyclical  
5  Consumer, Non-cyclical  
6  Consumer, Non-cyclical  
7  Consumer, Non-cyclical  
8                  Energy  
9  Consumer, Non-cyclical

Jegadeesh and Lakonishok (1996) showed that momentum may be explained by market’s underreaction to earning-related information as well.


<img src=https://alphaarchitect.com/wp-content/uploads/2015/01/2015-01-06-10_46_49-Chan-Jegadeesh-and-Lakonishok_1996.pdf-Adobe-Reader1.png width="500">

The Table above shows the results of a cross-sectional regressions of returns: the coefficient on past return is 5.7%. When introducing past earnings surprises, the coefficient decreases to 2.9%, but is still significant.

In [19]:
## read the date from Bloomberg about EPS Surprise Last Quarter
eps=pd.read_excel('Russell 2000 Index.xlsx', 'EPS Surprise%') 
eps.columns=["Ticker","Name","Weight","Shares","Price","EPS_SURP"]

In [20]:
eps=eps[["Ticker", "Name", "EPS_SURP"]]
eps.dropna(inplace=True)

## highlight in green positive earning surprise in parcentage term and red the negative surprise respect the estimations
def highlight(s):
    if s.EPS_SURP > 0:
        return ['background-color: springgreen']*3
    elif s.EPS_SURP < 0:
        return ['background-color: tomato']*3
    else:
        return ['background-color: white']*3
 
 
eps.style.apply(highlight, axis=1)

In [21]:
eps_top10=pd.merge(Final_TOP10,eps)
def highlight(s):
    if s.EPS_SURP > 0:
        return ['background-color: springgreen']*5
    elif s.EPS_SURP < 0:
        return ['background-color: tomato']*5
    else:
        return ['background-color: white']*5
 
 
eps_top10.style.apply(highlight, axis=1)

In [22]:
P_N_EPS= eps[ eps['EPS_SURP'] >=0 ] ## sort by positive and neutral Earnings Surprise % 
P_N_EPS
last_col=s.iloc[:,9:10]
last_col.columns=["Ticker"]
## pick companies that do not have the negative sentiment indicator 
P_N_news=pd.merge(last_col, P_N_news)
## pick companies 10 best companies within the previous group with Positive/Neutral EPS Surprise% 
Final_TOP10=pd.merge(P_N_news,P_N_EPS).iloc[0:10,] 

#### _Final Portofolio_ :

In [23]:
Final_TOP10

Ticker                          Name NEWS_SENTIMENT  \
0  BTAI UR Equity      BIOXCEL THERAPEUTICS INC       0.159411   
1  CCXI UW Equity              CHEMOCENTRYX INC              0   
2  MRSN UW Equity      MERSANA THERAPEUTICS INC              0   
3  ENPH UQ Equity            ENPHASE ENERGY INC              0   
4  SVRA UW Equity                    SAVARA INC              0   
5  KNSA UW Equity     KINIKSA PHARMACEUTICALS-A              0   
6  ITCI UW Equity  INTRA-CELLULAR THERAPIES INC              0   
7  CYCN UW Equity    CYCLERION THERAPEUTICS INC              0   
8  RTIX UW Equity          RTI SURGICAL HDS INC              0   
9  CALA UW Equity     CALITHERA BIOSCIENCES INC              0   

                 Industry   EPS_SURP  
0  Consumer, Non-cyclical   3.389831  
1  Consumer, Non-cyclical  21.428571  
2  Consumer, Non-cyclical   6.166220  
3                  Energy  28.440367  
4  Consumer, Non-cyclical  23.950617  
5  Consumer, Non-cyclical  30.268741  
6  Consumer, Non-cyclical  21.321696  
7  Consumer, Non-cyclical  23.076923  
8  Consumer, Non-cyclical   0.000000  
9  Consumer, Non-cyclical  14.988814

**Company Business Description**



<img src=https://cdn4.iconfinder.com/data/icons/basic-ui-elements-24/512/1001_Alert_danger_warning_sign-512.png width="70"> 

_The ranking changes every day, thus the business description below will be different. This is on 2020 March 06:_

- 1) BIOXCEL THERAPEUTICS INC:  operates as a biopharmaceutical company. The Company utilizes big data, machine learning, and artificial intelligence to identify the next wave of medicines for neuroscience, immuno-oncology, and related diseases. Bioxcel Therapeutics serves patients in the United States.


- 2) CHEMOCENTRYX INC: operates as a biopharmaceutical company. The Company researches orally-administered small-molecule therapies for inflammatory diseases.


- 3) MERSANA THERAPEUTICS INC: produces novel drug conjugates. The Company specializes in oncology agents for the treatment of tumors and cancer. Mersana Therapeutics serves the healthcare industry in the United States.


- 4) ENPHASE ENERGY INC: manufactures solar power solutions. The Company offers solutions to increase productivity and reliability of solar modules.


- 5) SAVARA INC: operates as a clinical-stage pharmaceutical company. The Company focuses on the development of novel therapies for the treatment of serious and life-threatening rare respiratory diseases. Savara offers its services worldwide.


- 6) KINIKSA PHARMACEUTICALS-A:  operates as a clinical-stage biopharmaceutical company. The Company focuses on discovering, acquiring, developing, and commercializing therapeutic medicines for patients suffering from debilitating diseases with significant unmet medical need. Kiniksa Pharmaceuticals serves patients worldwide.


- 7) INTRA-CELLULAR THERAPIES INC:  researches and develops biopharmaceutical drugs. The Company engages in the research and development of small molecule drugs to treat neuropsychiatric and neurological diseases and other disorders of the central nervous system. Intra-Cellular Therapies offers its products to the medical industry.


- 8) CYCLERION THERAPEUTICS INC: produces and distributes specialty pharmaceutical products. The Company offers its services in the United States.


- 9) RTI SURGICAL HDS INC: produces and distributes medical equipment. The Company offers products that are used by surgeons to repair bones and tissue defects such as vertebrae, fracture, and joint repair, as well as musculoskeletal reconstruction and sports medicine injury treatment. RTI Surgical Holdings serves patients in the United States.


- 10) CALITHERA BIOSCIENCES INC: provides pharmaceutical products. The Company is focused on discovering and developing novel small molecule drugs against tumor metabolism and immunology for the treatment of cancer. Calithera Biosciences serves patrients in the United States.